# Обучение нейросетей: Базовые приемы

In [ ]:
!curl -O 'https://courses.cv-gml.ru/storage/seminars/nn-training-basics/dataset.zip'

In [ ]:
!unzip -qo dataset.zip

In [ ]:
import glob

import matplotlib.pyplot as plt
import numpy as np
import PIL.Image
import torch
import torch.nn.functional as F
from torch import nn
from tqdm.auto import tqdm

# Increase these if figures appear small
plt.rcParams["figure.figsize"] = fx, fy = (14.08, 6.40)

# Not using `bfloat16` matrix multiplication for consistency
# You might get better performance without much precision loss
# by setting this to "medium" on some devices
torch.set_float32_matmul_precision("high")

In [ ]:
def show_images(images, titles=[]):
    num = len(images)
    fig, axs = plt.subplots(nrows=1, ncols=num, squeeze=True, layout="constrained")
    axs = [axs] if num <= 1 else axs
    for i in range(num):
        ax = axs[i]
        ax.imshow(images[i])
        ax.axis("off")
        if titles != []:
            ax.set_title(titles[i])

    plt.show(fig)
    plt.close(fig)

## Обучение простого классификатора на PyTorch

In [ ]:
CLASSES = {"cloudy": 0, "foggy": 1, "rainy": 2, "shine": 3, "sunrise": 4}

In [ ]:
weather_images = []
titles = []
for weather in CLASSES.keys():
    sample = sorted(glob.glob(f"./dataset/{weather}/*")).pop(0)
    weather_images.append(PIL.Image.open(sample))
    titles.append(weather)
show_images(weather_images, titles)

Научимся использовать свои данные при обучении, для этого необхимо создать свой собственный подкласс **`torch.utils.data.Dataset`**.

Также для подтверждения успешности обучения модели понадобится валидационная выборка, которая не должна пересекаться с обучающей.

In [ ]:
NETWORK_SIZE = (64, 64)
BATCH_SIZE = 16

if torch.cuda.is_available():
    DEVICE = torch.device("cuda")
    print("Using the GPU 😊")
else:
    DEVICE = torch.device("cpu")
    print("Using the CPU 😞")

In [ ]:
import torchvision.transforms.v2 as T

IMAGENET_MEAN = [0.485, 0.456, 0.406]
IMAGENET_STD = [0.229, 0.224, 0.225]
DEFAULT_TRANSFORM = T.Compose(
    [
        T.ToImage(),
        T.ToDtype(torch.float32, scale=True),
        T.Resize(size=NETWORK_SIZE),
        T.Normalize(mean=IMAGENET_MEAN, std=IMAGENET_STD),
    ]
)

In [ ]:
import random

from torch.utils import data


class MyCustomDataset(data.Dataset):
    def __init__(
        self,
        mode,
        root_dir="./dataset",
        train_fraction=0.8,
        split_seed=42,
        transform=None,
    ):
        # We can't store all the images in memory at the same time,
        # because sometimes we have to work with very large datasets
        # so we will only store data paths.

        paths = []
        labels = []
        rng = random.Random(split_seed)
        for cls_name, cls_idx in CLASSES.items():

            # Make sure that train and validation splits
            # use the same (random) order of samples
            cls_paths = sorted(glob.glob(f"{root_dir}/{cls_name}/*"))
            split = int(train_fraction * len(cls_paths))
            rng.shuffle(cls_paths)

            if mode == "train":
                cls_paths = cls_paths[:split]
            elif mode == "valid":
                cls_paths = cls_paths[split:]
            else:
                raise RuntimeError(f"Invalid mode: {mode!r}")

            paths.extend(cls_paths)
            labels.extend(cls_idx for _ in range(len(cls_paths)))

        self._len = len(paths)
        self._paths = paths
        self._labels = np.array(labels)
        assert self._labels.shape == (self._len,)

        if transform is None:
            transform = DEFAULT_TRANSFORM
        self._transform = transform

    def __len__(self):
        return len(self._paths)

    def __getitem__(self, index):
        img_path = self._paths[index]
        label = self._labels[index]

        # Read the image from disk
        image = np.array(PIL.Image.open(img_path).convert("RGB"))

        # Apply the desired transformations
        image = self._transform(image)

        return image, label

In [ ]:
import os

# Prepare the data
ds_train = MyCustomDataset(mode="train")
ds_valid = MyCustomDataset(mode="valid")

dl_train = data.DataLoader(
    ds_train,
    batch_size=BATCH_SIZE,
    shuffle=True,
    drop_last=True,
    num_workers=os.cpu_count(),
)
dl_valid = data.DataLoader(
    ds_valid,
    batch_size=BATCH_SIZE,
    shuffle=False,
    drop_last=False,
    num_workers=os.cpu_count(),
)

Будем использовать простую сверточную архитектуру

In [ ]:
class MyModel(nn.Sequential):
    def __init__(self, num_classes):
        super().__init__()

        self.conv1 = nn.Conv2d(3, 6, kernel_size=5)
        self.relu1 = nn.ReLU()
        self.pool1 = nn.MaxPool2d(kernel_size=2)

        self.conv2 = nn.Conv2d(6, 16, kernel_size=3)
        self.relu2 = nn.ReLU()
        self.pool2 = nn.MaxPool2d(kernel_size=2)

        self.conv3 = nn.Conv2d(16, 5, kernel_size=3, padding=1)
        self.relu3 = nn.ReLU()
        self.pool3 = nn.MaxPool2d(kernel_size=2)

        # (N, 5, 7, 7) -> (N, 5 * 7 * 7 == 245)
        self.flatten = nn.Flatten(start_dim=1, end_dim=-1)

        self.fc1 = nn.Linear(5 * 7 * 7, 120)
        self.relu4 = nn.ReLU()

        self.fc2 = nn.Linear(120, 84)
        self.relu5 = nn.ReLU()

        self.fc3 = nn.Linear(84, num_classes)

#### Дизайн / выбор архитектуры

<table style="font-size: 2rem;"><thead>
  <tr>
    <td style="border-right: solid 1px;"></td>
    <th style="text-align: center;">inference (production)</th>
    <th style="text-align: center;">training (development)</th>
  </tr></thead>
<tbody>
  <tr>
    <th style="border-right: solid 1px;">скорость работы<br/>(в FLOPs, FPS или seconds/sample)</th>
    <td style="text-align: center;">на целевом девайсе, с использованием<br/>inference-specific оптимизаций</td>
    <td style="text-align: center;">на девайсе для обучения, время<br/>необходимое на проведение экспериментов</td>
  </tr>
  <tr>
    <th style="border-right: solid 1px;">количество параметров<br/>(в штуках или байтах)</th>
    <td style="text-align: center;">размер приложения на диске,<br/>скорость загрузки на девайс</td>
    <td style="text-align: center;">репрезентативная способность модели,<br/>склонность к переобучению</td>
  </tr>
  <tr>
    <th style="border-right: solid 1px;">пиковое потребление памяти<br/>(в байтах или % от максимума)</th>
    <td style="text-align: center;">возможность "уместиться" на целевом девайсе,<br/>возможность параллельной обработки</td>
    <td style="text-align: center;">максимальный размер батча,<br/>требования к девайсу для обучения</td>
  </tr>
</tbody>
</table>

Все 6 пунктов - важны. Каждый из этих пунктов нетривиально зависит от выбора гиперпараметров и элементов дизайна архитектуры. В частности, обратите внимание, что все 6 пунктов в общем случае независимы и не обязаны коррелировать друг с другом (то есть они могут увеличиваться/уменьшаться независимо друг от друга). 

---

Тривиальный цикл для обучения на PyTorch (см. прошлый семинар)

In [ ]:
def train(num_epochs):
    # Prepare model and optimization stuff
    model = MyModel(num_classes=len(CLASSES)).to(DEVICE)
    loss_fn = torch.nn.CrossEntropyLoss().to(DEVICE)
    optimizer = torch.optim.Adam(model.parameters(), lr=1e-3)

    # The main loop
    for e in range(num_epochs):

        # Train for a single epoch
        model = model.train()
        train_loss = []
        progress_train = tqdm(
            total=len(dl_train),
            desc=f"Epoch {e}",
            leave=False,
        )
        for x_batch, y_batch in dl_train:
            x_batch = x_batch.to(DEVICE)
            y_batch = y_batch.to(DEVICE)

            p_batch = model(x_batch)
            loss = loss_fn(p_batch, y_batch)
            train_loss.append(loss.detach())

            loss.backward()
            optimizer.step()
            optimizer.zero_grad()

            progress_train.update()
        progress_train.close()

        train_loss = torch.stack(train_loss).mean()
        print(
            f"Epoch {e},",
            f"train_loss: {train_loss.item():.8f}",
        )

        # Measure metrics on validation
        model = model.eval()
        valid_accs = []
        progress_valid = tqdm(
            total=len(dl_valid),
            desc=f"Epoch {e}",
            leave=False,
        )
        for x_batch, y_batch in dl_valid:
            x_batch = x_batch.to(DEVICE)
            y_batch = y_batch.to(DEVICE)

            with torch.no_grad():
                p_batch = model(x_batch)

            matches = p_batch.argmax(axis=-1) == y_batch
            valid_accs.append(matches)

            progress_valid.update()
        progress_valid.close()

        valid_accs = torch.concat(valid_accs).float().mean()
        print(
            f"Epoch {e},",
            f"valid_accs: {valid_accs.item():.8f}",
        )

    return model

In [ ]:
model = train(num_epochs=3)

Сохранение и загрузка параметров

In [ ]:
# Get all of the current model parameters
sd = model.state_dict()
print(list(sd.keys()))

In [ ]:
print(sd["conv1.bias"])
print()
print(model.conv1.bias)

In [ ]:
# Save the parameters to disk
torch.save(sd, "model.pt")

In [ ]:
# This is WRONG!
if False:
    torch.save(model, "dont_do_this.pt")

# This "kind of" works, but it pickles the whole MyModel
# object itself, instead of only saving the parameters.
# This is almost never what you actually want.

In [ ]:
# Re-create the model object from scratch
model = MyModel(num_classes=len(CLASSES))

# Load the saved parameters
#
# WARNING!
# By default, torch.load uses pickle which
# can cause arbitrary code execution.
#
# NEVER use torch.load without explicitly setting
# weights_only=True. Alternatively, consider using
# safetensors when loading parameters from
# unknown/untrusted sources.
sd = torch.load(
    "model.pt",
    map_location=DEVICE,
    weights_only=True,
)
model.load_state_dict(sd);

---

## PyTorch Lightning

<img src="https://courses.cv-gml.ru/storage/seminars/nn-training-basics/lightning_logo.png" width="50%">

### Почему PyTorch Lightning?

#### Много реализованного функционала

* Обучение на GPU/нескольких GPU/TPU 

* Multi-node training

* Авто логгирование

* Gradient accumulation

* …

#### Меньше boilerplate кода

Любое исследование можно начать с простого кода и быстро добавить более сложные (уже реализованные) вещи, такие как: обучение на GPU, 16-bit, сохрание чекпоинтов, логгирование, …

PyTorch Lightning сделал и протестировал много всего за Вас, чтобы Вы могли сосредоточиться на исследовании других идей.

Меньше инженерного кода означает:

* меньше багов

* более быстрое итерирование и прототипирование

#### Стандартная структура кода

PyTorch Lightning задает дефолтную "opinionated" схему организации кода. Переходя в новый проект не нужно с нуля разбираться в том, как авторы переизобрели велосипед. Callback функции имеют предсказуемые имена, меньше глобальных объектов, меньше магических констант и тп.

In [ ]:
import lightning as L


# Direct translation of the previous train function
class MyTrainingModule(L.LightningModule):
    def __init__(self):
        super().__init__()
        self.model = MyModel(num_classes=len(CLASSES))
        self.train_loss = []
        self.valid_accs = []

    def configure_optimizers(self):
        return torch.optim.Adam(self.model.parameters(), lr=1e-3)

    def training_step(self, batch):
        x, y = batch
        p = self.model(x)
        loss = F.cross_entropy(p, y)
        self.train_loss.append(loss.detach())
        return loss

    def validation_step(self, batch):
        x, y = batch
        p = self.model(x)
        matches = p.argmax(axis=-1) == y
        self.valid_accs.append(matches)
        return {}

    def on_train_epoch_end(self):
        epoch_loss = torch.stack(self.train_loss).mean()
        print(
            f"Epoch {self.trainer.current_epoch},",
            f"train_loss: {epoch_loss.item():.8f}",
        )
        # don't forget to clear the saved losses
        self.train_loss.clear()

    def on_validation_epoch_end(self):
        epoch_accs = torch.concat(self.valid_accs).float().mean()
        print(
            f"Epoch {self.trainer.current_epoch},",
            f"valid_accs: {epoch_accs.item():.8f}",
        )
        # don't forget to clear the saved accuracies
        self.valid_accs.clear()

In [ ]:
# Init our training module
training_module = MyTrainingModule()

# Initialize a trainer
trainer = L.Trainer(accelerator="auto", max_epochs=3)

# Train the model ⚡
trainer.fit(training_module, dl_train, dl_valid)

### Возобновление обучения

Как уже было сказано выше в Pytorch Lightning реализовано автоматическое логгирование.

Сохранены все запуски: 

In [ ]:
!tree lightning_logs/

Как видите, Lightning автоматически сохранил чекпоинт последней эпохи. Если прервать обучение, то все равно будет сохранены результаты с последней успешно завершившейся эпохи.

Обратите внимание, что чекпоинт - это не просто веса обученной модели. Например, в чекпоинт также включаются статистики оптимизатора. Таким образом, используя чекпоинт можно возобновить прерванный процесс обучения.

In [ ]:
last_ckpt = "lightning_logs/version_0/checkpoints/epoch=2-step=225.ckpt"
ckpt = torch.load(last_ckpt, weights_only=True, map_location=DEVICE)
print(list(ckpt.keys()))

In [ ]:
# Continue training the model for 2 more epochs
training_module = MyTrainingModule()
trainer = L.Trainer(accelerator="auto", max_epochs=5)
trainer.fit(training_module, dl_train, dl_valid, ckpt_path=last_ckpt)

In [ ]:
training_module = MyTrainingModule.load_from_checkpoint(last_ckpt, map_location=DEVICE)

In [ ]:
training_module.model

### Идиоматичный подсчет метрик

In [ ]:
import torchmetrics


class MyTrainingModule(L.LightningModule):
    def __init__(self, num_classes=len(CLASSES)):
        super().__init__()
        self.model = MyModel(num_classes=num_classes)
        self.accuracy = torchmetrics.classification.Accuracy(
            task="multiclass",
            num_classes=num_classes,
        )

    def configure_optimizers(self):
        return torch.optim.Adam(self.model.parameters(), lr=1e-3)

    def training_step(self, batch):
        return self._step(batch, "train")

    def validation_step(self, batch):
        return self._step(batch, "valid")

    def _step(self, batch, kind):
        x, y = batch
        p = self.model(x)
        loss = F.cross_entropy(p, y)
        accs = self.accuracy(p.argmax(axis=-1), y)

        metrics = {
            f"{kind}_accs": accs,
            f"{kind}_loss": loss,
        }
        self.log_dict(
            metrics,
            prog_bar=True,
            logger=True,
            on_step=kind == "train",
            on_epoch=True,
        )

        return loss

In [ ]:
def my_progress_bar():
    return L.pytorch.callbacks.TQDMProgressBar(leave=True)

In [ ]:
training_module = MyTrainingModule()
trainer = L.Trainer(
    accelerator="auto",
    max_epochs=3,
    callbacks=[my_progress_bar()],
    # Make on_step log *literally* every step
    # (since our dataset is so small)
    log_every_n_steps=1,  # for demonstration puproses only
)
trainer.fit(training_module, dl_train, dl_valid)

### Tensorboard

Tensorboard - популярный инструментарий для визуализации различных объектов получаемых в процессе обучения. В Lightning по умолчанию включено автоматическое сохранения логов в формате Tensorboard. Кроме того, в Lightning есть поддержка для ряда других библитоек логирования (WandB, Comet, MLFlow, Neptune, простой CSV или даже свой кастомный логгер).

Tensorboard можно запустить, выполнив комманду `tensorboard` в терминале и открыв распечатанную ссылку в браузере (обычно, http://localhost:6006/).

Либо, используя специальное расширение для Jupyter, можно открыть Tensorboard как embedded окошечко для прямо в ноутбуке:

In [ ]:
%load_ext tensorboard

In [ ]:
%tensorboard --logdir lightning_logs

### Расписание learning rate

При обучении нейронной сети полезно постепенно снижать темп обучения для того, чтобы более точно попасть в локальный минимум.

Снижают learning rate по определенным правилам. Достаточно часто используют один из следующих подходов:

- **time-based decay**
  $$\alpha(step) = \alpha_0\ {\cdot}\ \frac{1}{1 + \gamma{\cdot}step}$$
  <br/>

- **smooth exponential decay**
  $$\alpha(step) = \alpha_0\ {\cdot}\ {\gamma}^{step} \qquad (0 < \gamma < 1)$$
  <br/>

- **stepwise exponential decay**
  $$\alpha(step) = \alpha_0\ {\cdot}\ {\gamma}^{\left\lfloor\frac{step}{interval}\right\rfloor} \qquad (\text{e.g. }\ \gamma = 0.1,\ \ interval \propto epoch)$$
  <br/>

- **plateau decay**
  $$
      \alpha(0) = \alpha_0\\
      \alpha(epoch) = \begin{cases}
          \alpha(epoch - 1)\ {\cdot}\ \gamma\quad\text{if metrics didn't improving for }P\text{ epochs}\\
          \alpha(epoch - 1)\quad\quad\text{otherwise}
      \end{cases}
  $$

<br/>
<img src="https://courses.cv-gml.ru/storage/seminars/nn-training-basics/lr_schedulers.png" width="50%">

In [ ]:
class MyTrainingModule_WithLRScheduler(MyTrainingModule):
    def configure_optimizers(self):
        optimizer = super().configure_optimizers()

        lr_scheduler = torch.optim.lr_scheduler.StepLR(
            optimizer,
            # decay the LR every five epochs
            step_size=5,
            gamma=0.1,
        )

        lr_scheduler_config = {
            "scheduler": lr_scheduler,
            # The unit of the scheduler's step size, could also be 'step'.
            # 'epoch' updates the scheduler on epoch end whereas 'step'
            # updates it after a optimizer update.
            "interval": "epoch",
            # How many epochs/steps should pass between calls to
            # `scheduler.step()`. 1 corresponds to updating the learning
            # rate after every `interval` (epoch or step).
            "frequency": 1,
            ## Metric to to monitor for schedulers like `ReduceLROnPlateau`
            # "monitor": "valid_accs",
        }

        return [optimizer], [lr_scheduler_config]

In [ ]:
def my_lr_monitor():
    return L.pytorch.callbacks.LearningRateMonitor()

In [ ]:
training_module = MyTrainingModule_WithLRScheduler()
trainer = L.Trainer(
    accelerator="auto",
    max_epochs=10,
    callbacks=[my_progress_bar(), my_lr_monitor()],
    log_every_n_steps=1,  # for demonstration puproses only
)
trainer.fit(training_module, dl_train, dl_valid)

### Кастомизация чекпоинтов

Мы уже видели, что Pytorch Lightning сохраняет веса модели самостоятельно. Однако сохраняются веса только последней эпохи, метрики на которой могут быть не максимальны, чтобы это исправить самостоятельно напишем callback **`ModelCheckpoint`**.

Также воспользуемся **`EarlyStopping`** для того, чтобы обучение останавливалось при отсутствие роста метрик в течение нескольких эпох.

In [ ]:
def my_training_checkpoint():
    # Save the training module periodically by monitoring a quantity.
    return L.pytorch.callbacks.ModelCheckpoint(
        filename="{epoch}-{valid_accs:.3f}",
        monitor="valid_accs",
        mode="max",
        save_top_k=1,
        save_last=True,
    )


def my_early_stopping():
    # Monitor a metric and stop training when it stops improving.
    return L.pytorch.callbacks.EarlyStopping(
        monitor="valid_accs",
        mode="max",
        patience=4,
        verbose=True,
    )

In [ ]:
training_module = MyTrainingModule_WithLRScheduler()
trainer = L.Trainer(
    max_epochs=100,
    accelerator="auto",
    callbacks=[
        my_progress_bar(),
        my_lr_monitor(),
        my_training_checkpoint(),
        my_early_stopping(),
    ],
    log_every_n_steps=1,  # for demonstration puproses only
)
trainer.fit(training_module, dl_train, dl_valid)

In [ ]:
!tree lightning_logs/

------

<img src="https://courses.cv-gml.ru/storage/seminars/nn-training-basics/albumentations_logo.png" width="50%">

## Почему Albumentations?
Albumentations - это Python библиотека для быстрого и гибкого аугментирования изображений. Albumentations эффективно реализует широкий спектр операций преобразования изображений и обеспечивает при этом лаконичный, но мощный интерфейс для различных задач компьютерного зрения, включая классификацию, сегментацию и детекцию.

### Пример аугментаций из Albumentations:

![](https://courses.cv-gml.ru/storage/seminars/nn-training-basics/albumentations_1.png)

### Пример использования:

In [ ]:
import albumentations as A

In [ ]:
MyTransform = A.Compose(
    [
        A.RandomResizedCrop(size=(128, 128), p=0.3),
        A.Rotate(limit=30),
        A.HorizontalFlip(p=0.3),
        A.RandomBrightnessContrast(brightness_limit=0.3, contrast_limit=0.3, p=0.5),
    ]
)

In [ ]:
show_images(weather_images, titles)
for _ in range(4):
    transformed = [
        MyTransform(image=np.array(image))["image"]
        for image in weather_images
        #
    ]
    show_images(transformed)

In [ ]:
MyTransform = A.Compose(
    [
        A.SmallestMaxSize(max_size=160),
        A.Affine(translate_percent=0.05, scale=(1.0, 1.05), rotate=15, p=0.5),
        A.RandomCrop(height=128, width=128),
        A.RGBShift(r_shift_limit=15, g_shift_limit=15, b_shift_limit=15, p=0.5),
        A.RandomBrightnessContrast(brightness_limit=0.3, contrast_limit=0.3, p=0.5),
        A.HorizontalFlip(p=0.3),
    ]
)

In [ ]:
show_images(weather_images, titles)
for _ in range(4):
    transformed = [
        MyTransform(image=np.array(image))["image"]
        for image in weather_images
        #
    ]
    show_images(transformed)

#### Ковариантное преобразование изображений и меток

![](https://courses.cv-gml.ru/storage/seminars/nn-training-basics/albumentations_2.png)

------

### Добавим аугментации в обучение

In [ ]:
import albumentations.pytorch.transforms

augmentations = [
    A.SmallestMaxSize(max_size=160),
    A.Affine(translate_percent=0.05, scale=(1.0, 1.05), rotate=15, p=0.5),
    A.RandomCrop(height=128, width=128),
    A.RGBShift(r_shift_limit=15, g_shift_limit=15, b_shift_limit=15, p=0.5),
    A.RandomBrightnessContrast(brightness_limit=0.3, contrast_limit=0.3, p=0.5),
    A.HorizontalFlip(p=0.3),
]
# Don't forget to prepare the image data for consumption by PyTorch
common_transforms = [
    A.Resize(*NETWORK_SIZE),
    A.ToFloat(max_value=255),
    A.Normalize(max_pixel_value=1.0, mean=IMAGENET_MEAN, std=IMAGENET_STD),
    A.pytorch.transforms.ToTensorV2(),
]

MyTrainTransform = A.Compose(augmentations + common_transforms)
MyValidTransform = A.Compose(common_transforms)

In [ ]:
def my_train_transform(image):
    return MyTrainTransform(image=image)["image"]


def my_valid_transform(image):
    return MyValidTransform(image=image)["image"]


ds_train_alb = MyCustomDataset(
    mode="train",
    transform=my_train_transform,
)
ds_valid_alb = MyCustomDataset(
    mode="valid",
    transform=my_valid_transform,
)

dl_train_alb = data.DataLoader(
    ds_train_alb,
    batch_size=BATCH_SIZE,
    shuffle=True,
    drop_last=True,
    num_workers=os.cpu_count(),
)
dl_valid_alb = data.DataLoader(
    ds_valid_alb,
    batch_size=BATCH_SIZE,
    shuffle=False,
    drop_last=False,
    num_workers=os.cpu_count(),
)

In [ ]:
training_module = MyTrainingModule_WithLRScheduler()
trainer = L.Trainer(
    max_epochs=100,
    accelerator="auto",
    callbacks=[
        my_progress_bar(),
        my_lr_monitor(),
        my_training_checkpoint(),
        my_early_stopping(),
    ],
    log_every_n_steps=1,  # for demonstration puproses only
)
trainer.fit(training_module, dl_train_alb, dl_valid_alb)

---